# Amat Samuel

# Espacios invariantes para ecuaciones lineales 

Consideremos de nuevo la ecuación lineal

$$\dot{\mathbf{x}} = \mathsf{A} \cdot \mathbf{x}$$

Como hemos visto, los eigenvectores de $\mathsf{A}$ juegan un papel importante.

**[1]** (i) Dibuja el espacio fase del sistema $$\dot{\mathbf{x}} = \mathsf{A} \cdot \mathbf{x}$$ con 
$$A = \begin{pmatrix} 1 & 1 \\ 4 & -2 \end{pmatrix}. $$

(ii) Agrega el punto fijo.

(iii) Calcula los eigenvectores y eigenvalores de $\mathsf{A}$. 

(iv) Dibuja los eigenvectores encima de la gráfica del inciso (i). ¿Qué observas? ¿Qué concluyes?

### Solución

la ecuación diferencial anterior corresponde al siguiente sistema de ecuaciones:
\begin{eqnarray}
\dot{x} = x + y \\
\dot{y} = 4x - 2y
\end{eqnarray} 
A continuación se muestra el campo vectorial asociado al sistema de ecs. de arriba, i.e el espacio fase.

In [1]:
using DifferentialEquations
using Plots
using ForwardDiff
plotly()
include("funciones_especiales.jl")

estabilidad_nolineal2D (generic function with 1 method)

In [2]:
#sistema de ecs. diferenciales no-lineales
function RHS1(du::Array{Float64,1}, u::Array{Float64,1}, p::Void, t::Float64)
        du[1] = u[1] + u[2]
        du[2] = 4u[1] - 2u[2]
end
#jacobiano
A1(u) = [1. 1.; 4. -2.]

A1 (generic function with 1 method)

In [3]:
X = linspace(-100, 100, 10)
Y = linspace(-100, 100, 10)
xlim = (-100., 100.)
ylim = (-100., 100.)
tmax = 1.
h = 0.01
k = 10.
plot(xlims=xlim, ylims=ylim)
estabilidad_nolineal2D(RHS1, A1, X, Y, k, tmax, h)

#### Los vectores propios separan el comportamiento del campo en regiones distintas. En general se observa que los vectores propios se comportan como espacios vectoriales desde donde divergen y a donde convergen las soluciones

Lo que acabas de calcular son los **espacios invariantes** del sistema dinámico descrito por la ecuación diferencial:

- el **espacio estable** consiste en el span de los eigenvectores cuyos eigenvalores corresponden a las "direcciones estables", es decir aquellas con parte real negativa;

- el **espacio inestable**, correspondiente a la parte real positiva.

**[2]** (i) Considera una trayectoria que empieza encima del espacio estable. ¿Qué ocurre? Hazlo numéricamente.

(ii) Haz lo mismo para el espacio inestable.

### Solución

In [4]:
tmax=1.
pto = [0.,0.]
A = A1(pto)
ux = [90.*eig(A)[2][1,1]]#, 90.*eig(A)[2][1,2]]
uy = [90.*eig(A)[2][2,1]]#, 90.*eig(A)[2][2,2]]
cond_init = [[ux[i], uy[j]] for i=1:length(ux), j=1:length(uy)]
solx=[]
soly=[]
for i in 1:length(cond_init)
    prob = ODEProblem(RHS1, cond_init[i], (0, tmax))
    sol = solve(prob, saveat=h)
    a = [sol.u[i][1] for i = 1:length(sol.u)]
    sols = hcat(a, [sol.u[i][2] for i =1:length(sol.u)])
    solx = sols[:,1]
    soly = sols[:,2]
end
scatter(solx, label="λ>0", color=:red, xlabel="tiempo", ylabel="coordenadas")
p1 = scatter!(soly, label="", color=:red, title="espacio inestable")

ux = [90.*eig(A)[2][1,2]]#, 90.*eig(A)[2][1,2]]
uy = [90.*eig(A)[2][2,2]]#, 90.*eig(A)[2][2,2]]
cond_init = [[ux[i], uy[j]] for i=1:length(ux), j=1:length(uy)]
solx=[]
soly=[]
for i in 1:length(cond_init)
    prob = ODEProblem(RHS1, cond_init[i], (0, tmax))
    sol = solve(prob, saveat=h)
    a = [sol.u[i][1] for i = 1:length(sol.u)]
    sols = hcat(a, [sol.u[i][2] for i =1:length(sol.u)])
    solx = sols[:,1]
    soly = sols[:,2]
end
scatter(solx, label="λ<0", xlabel="tiempo", ylabel="coordenadas", color=:blue)
p2 = scatter!(soly, label="", color=:blue, title="espacio estable")
plot(p1, p2)

#### Se observa que cuando la condición inicial se encuentra sobre el vector propio asociado al valor propio negativo $\lambda<0$, las coordenas de $x$, $y$ se acercan asintóticamente al pto fijo $x^* = (0,0)$. Mientras que si comenzamos en el espacio inestable $\lambda>0$ entonces las coordenadas se alejan del punto fijo.

## Sistemas nolineales

Ahora consideremos el caso general, un sistema nolineal

$$\dot{\mathbf{x}} = \mathbf{f}(\mathbf{x}).$$

Si sabemos que tiene un punto fijo $\mathbf{x}^*$, podemos hacer el análisis de estabilidad lineal ahí, que hasta ahora nos ha servido para encontrar si es un punto fijo estable o inestable. 

Sin embargo, va más allá que eso: sea $\mathsf{J} := D\mathbf{f}(\mathbf{x}^*)$ la matrix jacobiana en el punto fijo. Entonces la ecuación

$$\dot{\mathbf{x}} = \mathsf{J} \cdot \mathbf{x}$$

se llama el **sistema linealizado** en el punto fijo.


**[3]** Considera de nuevo la ecuación

\begin{align}
\dot{x} &= x + \exp(-y)\\
\dot{y} &= -y
\end{align}

(i) Dibuja el espacio fase del sistema nolineal, incluyendo el punto fijo.

(ii) Encuentra el sistema linealizado en el punto fijo, y dibuja su espacio fase encima, cerca del punto fijo.

(iii) Dibuja los espacios invariantes del sistema linealizado encima. ¿Qué observas?

### Solución.

In [5]:
function RHS2(du::Array{Float64,1}, u::Array{Float64,1}, p::Void, t::Float64)
        du[1] = u[1] + exp(-u[2])
        du[2] = -u[2]
end
J2(u) = [1 -exp(-u[2]); 0 -1]

J2 (generic function with 1 method)

In [6]:
function RHS2_linealizado(du::Array{Float64,1}, u::Array{Float64,1}, p::Void, t::Float64)
        du[1] = (u[1] + 1.) - (u[2] - 0.)
        du[2] = -(u[2] - 0.)
end

RHS2_linealizado (generic function with 1 method)

In [7]:
X = linspace(-2.4, 0.6, 8)
Y = linspace(-1.4, 1.4, 8)
xlim = (-2.4, 0.6)
ylim = (-1.4, 1.4)
tmax = 4.
h = 0.1
k=4.
plot(xlims=xlim, ylims=ylim, title="linealizado")
p1 = estabilidad_nolineal2D(RHS2_linealizado, J2, X, Y, k, tmax, h)
plot(xlims=xlim, ylims=ylim, title="no lineal")
p2 = estabilidad_nolineal2D(RHS2, J2, X, Y, k, tmax, h)
plot(p1, p2)

#### Izquierda se muestra el sistema linealizado junto con los dos espacios invariantes dados por los generados de cada vector propio (i.e rectas punteadas).
#### Derecha se muestra el sistema original (no lineal).
#### Vemos que el cerca del punto fijo (haciendo un zoom con plotly) en el sistema no lineal los espacios invariantes parecen ser correctos, es decir, el sistema se aproxima y aleja respectivamente de c/u de ellos asintóticamente, pero al ver el sistema más de lejos vemos, que esto falla.

#### NOTA: no encimé las gráficas como se pide porque no era claro el análisis por la confusión entre campos lineal y no lineal, espero se entienda

## El teorema de Hartman&ndash;Grobman

Debes haber observado en el inciso [2] que el comportamiento de los sistemas nolineal y linealizado se parecen cerca del punto fijo.

La idea es que cerca del punto fijo, el sistema nolineal se puede desarrollar:

$$\dot{\mathbf{x}} = [D\mathbf{f}(\mathbf{x}^*)] \cdot \mathbf{x} + O(\mathbf{\delta x}^2),$$

donde los términos nolineales son chiquitos.
Por lo tanto, uno podría esperar que las dinámicas de los sistemas nolineales y linealizados fueran parecidas cerca del punto fijo, ya que ahí la diferencia en la dinámica es pequeña.


El teorema de Hartman&ndash;Grobman hace rigurosaesta idea.

La

Primero, definimos un **punto fijo hiperbólico** $\mathbf{x}^*$ como un punto fijo tal que ningún eigenvalor de la matriz jacobiano en ese punto se encuentre en el eje imaginario.

El teorema dice:
> Si $\mathbf{x}^*$ es un punto fijo hiperbólico de la ecuación $\dot{\mathbf{x}} = \mathbf{f}(\mathbf{x})$, entonces cerca del punto fijo, el flujo de la ecuación nolineal "se parece" al flujo de la ecuación lineal.

Aquí, "se parece" quiere decir que existe un homeomorfismo (función continua e invertible) que lleva órbitas del sistema lineal a órbitas del sistema nolineal.

Nótese que en general esto ** *no* es cierto cuando el punto fijo es no-hiperbólico **.

## Variedades invariantes

Dado el teorema de Hartman&ndash;Grobman, debe existir un análogo en el sistema nolineal de los espacios estable e inestable del sistema lineal. Estas curvas deben obtenerse al mapear las trayectorias correspondientes a estos espacios invariantes bajo el homeomorfismo.

Estas curvas (o variedades, en general) son entonces "versiones curveadas" de los espacios invariantes.

**[4]** 

(i) ¿Cómo se pueden definir las variedades invariantes en términos de su comportamiento asintótico?

(ii) Muy cerca del punto fijo, las variedades invariantes son casi idénticas a los espacios invariantes. 

Utiliza esta idea para calcular las variedades invariantes de la ecuación del inciso **[3]**. 

(iii) Dibuja las variedades invariantes y los espacios invariantes. ¿Qué observas?

(iv) Dibuja el espacio fase completo del sistema nolineal.

### Solución

#### Las variedades invariantes cumplen ser los espacios vectoriales desde los cuales las souciones tienden asintóticamente al punto fijo (estables) o se alejan de él (inestables).
#### Utilizando la idea del teorema de HG, podemos colocarnos sobre el espacio invariante estable cerca del punto fijo y propagar una solución hacia atrás en el tiempo, eso construye la variedad estable. Análogamente, colocándonos en el espacio invariante inestable muy cerca del punto fijo, propagando hacia adelante en el tiempo podemos encontrar la variedad estable.

In [8]:
function variedades_invariantes(RHS, J, meshx, meshy, k, tmax, h)
    pts = PFs_estabilidad(RHS, J, meshx, meshy, "eigenvalor")
    pts_eig = PFs_estabilidad(RHS, J, meshx, meshy, "eigenvector")
    pts_hiperb = pts_eig["silla"] 
    v1 = pts_hiperb[1][:,1]
    λ1 = pts_hiperb[2][1]
    m1 = v1[2]/v1[1]
    v2 = pts_hiperb[1][:,2]
    λ2 = pts_hiperb[2][2]
    m2 = v2[2]/v2[1]
    v3 = pts["silla"][1]
    l1 = l2 = ""
    if λ1 < 0
        l1 = "espacio estable"
        l2 = "espacio inestable"
    else
        l1 = "espacio inestable"
        l2 = "espacio estable"
    end
    δx = 1e-4
    #variedades estables, se propaga a tiempos negativos
    ux = linspace(v3[1] + δx, v3[1] + δx, 1)
    uy = linspace(-m2*δx + v3[2], m2*δx + v3[2], 2)
    #for i in pts_eig["silla"]
     #   if pts_eig["silla"]
    cond_init = [[ux[i], uy[j]] for i=1:length(ux), j=1:length(uy)]
    for i in 1:length(cond_init)
        prob = ODEProblem(RHS, cond_init[i], (0., -2*tmax))
        sol = solve(prob, Tsit5())
        a = [sol.u[i][1] for i = 1:length(sol.u)]
        sols = hcat(a, [sol.u[i][2] for i =1:length(sol.u)])
        solx = sols[:,1]
        soly = sols[:,2]
        plot!(solx, soly, lw=2, linestyle=:dash, label="variedad estable", color=:blue)
    end
    #variedad inestable, se propaga a tiempos positivos
    ux = linspace(v3[1] + δx, v3[1] - δx, 2)
    uy = linspace(-m1*δx + v3[2], -m1*δx + v3[2], 1)
    cond_init = [[ux[i], uy[j]] for i=1:length(ux), j=1:length(uy)]
    for i in 1:length(cond_init)
        prob = ODEProblem(RHS, cond_init[i], (0., 2*tmax))
        sol = solve(prob, Tsit5())
        a = [sol.u[i][1] for i = 1:length(sol.u)]
        sols = hcat(a, [sol.u[i][2] for i =1:length(sol.u)])
        solx = sols[:,1]
        soly = sols[:,2]
        plot!(solx, soly, lw=2, linestyle=:dash, label="variedad inestable", color=:red)
    end
    
    campo(RHS, meshx, meshy, k, tmax, h)
    plot!(meshx, x->(m1*(x-v3[1])+v3[2]), label=l1, linestyle=:dash, lw=2)
    plot!(meshx, x->(m2*(x-v3[1])+v3[2]), label=l2, linestyle=:dash ,lw=2)
end

variedades_invariantes (generic function with 1 method)

In [9]:
X = linspace(-2., 0., 10)
Y = linspace(-1.0, 1.0, 10)
xlim = (-2., 0.)
ylim = (-1.0, 1.0)
tmax = 5.
h = 0.01
k=4.
plot(xlims=xlim, ylims=ylim)
variedades_invariantes(RHS2, J2, X, Y, k, tmax, h)

#### Vemos en cambio que ahora la variedad estable no tiene problemas para puntos lejanos al punto fijo, sigue cumpliendo separar el comportamiento del campo en regiones distintas, es decir, actúa como separatriz, a diferencia del espacio estable que sólo funciona bien cerca del punto fijo!